In [2]:
import pandas as pd
import numpy as np
import pandas_profiling as pd_prof
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_val_score
from sklearn.tree import DecisionTreeClassifier

In [124]:
train = pd.read_csv("train_1.csv", sep="\t", index_col="Unnamed: 0")
test = pd.read_csv("test_1.csv", sep="\t", index_col="Unnamed: 0")

In [185]:
train.head()

0  1  2  3  4  5  6         7  8  9 ...        336  337  338  339  340  \
0  1  1  0  0  0  0  0  0.090909  0  0 ...   0.221395    0    1    0    0   
1  1  1  0  0  1  0  0  0.090909  0  0 ...   0.241508    0    1    0    0   
2  0  1  0  0  1  0  0  0.090909  0  0 ...   0.123067    0    1    0    0   
3  0  1  0  0  1  0  0  0.136364  0  0 ...   0.296065    0    0    1    0   
4  0  1  0  0  1  0  0  0.136364  0  0 ...   0.178956    0    0    1    0   

        341  342  343  344  345  
0  0.222222    1    1    1    1  
1  0.111111    1    1    1    0  
2  0.444444    1    1    1    1  
3  0.222222    1    1    1    0  
4  0.111111    1    1    1    1  

[5 rows x 346 columns]

In [13]:
x_train_raw = train.iloc[:, 1:]
y_train_raw = train.iloc[:, 0]

In [14]:
x_train_raw.shape, y_train_raw.shape

((30500, 345), (30500,))

In [250]:
x_train_raw['114'].head()


0    0.100401
1    0.025549
2    0.041802
3    0.056071
4    0.107351
Name: 114, dtype: float64

In [16]:

pr = pd_prof.ProfileReport(x_train_raw)
pr

In [18]:
rejected_variables = pr.get_rejected_variables(threshold=0.99)
print(rejected_variables)

['153', '165', '180', '9']


In [239]:
rejected_variables = ['140', '152', '160', '164', '9', '153']

In [240]:
x_train_full = x_train_raw
x_train = x_train_raw.drop(rejected_variables, axis=1, errors='ignore')
x_train_full.shape, x_train.shape


((30500, 345), (30500, 339))

In [286]:
kf = StratifiedKFold(n_splits=7, random_state=42)

In [71]:
list(kf.split(x_train, y_train))

[(array([ 6034,  6035,  6037, ..., 30497, 30498, 30499]),
  array([   0,    1,    2, ..., 6392, 6397, 6401])),
 (array([    0,     1,     2, ..., 30497, 30498, 30499]),
  array([ 6034,  6035,  6037, ..., 12220, 12222, 12224])),
 (array([    0,     1,     2, ..., 30497, 30498, 30499]),
  array([12191, 12192, 12193, ..., 18374, 18382, 18386])),
 (array([    0,     1,     2, ..., 30497, 30498, 30499]),
  array([18288, 18289, 18290, ..., 24413, 24414, 24415])),
 (array([    0,     1,     2, ..., 24413, 24414, 24415]),
  array([24298, 24300, 24308, ..., 30497, 30498, 30499]))]

In [241]:
lr = LogisticRegression(random_state=42, class_weight= 'balanced')

In [242]:
scores_lr = cross_val_score(
    estimator=lr,
    X=x_train, # ...
    y=y_train, # ...
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('LR scoring: {:.5f}'.format(scores_lr))

LR scoring: 0.72442


In [47]:
## Decision Tree
dt = DecisionTreeClassifier(max_depth=25, random_state=42)


In [48]:
scores_dt = cross_val_score(estimator=dt,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('dt scoring: {:.5f}'.format(scores_dt))

dt scoring: 0.53541


In [195]:
##Random Forest
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
rf = RandomForestClassifier(random_state=42, class_weight='balanced')

In [196]:
scores_rf = cross_val_score(estimator=rf,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('rf scoring: {:.5f}'.format(scores_rf))

rf scoring: 0.67288


In [192]:
rf_fred = RandomForestClassifier(random_state=42, max_depth=15, min_samples_leaf=5, max_features=0.33, n_estimators=50, class_weight='balanced')


In [193]:
scores_rf_fred = cross_val_score(estimator=rf_fred,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('fred\'s rf scoring: {:.5f}'.format(scores_rf_fred))

fred's rf scoring: 0.72764


In [243]:
## Grid Search
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
params = {
    'max_depth':[15,20, 32, None],
    'min_samples_leaf': [8,16, 32, 64],
    'max_features': [0.33, 0.50, 0.66, 1.0],
    'n_estimators': [32, 64]
    
    
}
gs = RandomizedSearchCV(estimator=RandomForestClassifier(random_state=42, class_weight='balanced'), param_distributions=params, n_jobs=8, cv=kf, scoring='roc_auc', verbose=2, random_state=42)
gs.fit(x_train, y_train)

Fitting 5 folds for each of 10 candidates, totalling 50 fits
[CV] n_estimators=64, min_samples_leaf=64, max_features=0.66, max_depth=20 
[CV] n_estimators=64, min_samples_leaf=64, max_features=0.66, max_depth=20 
[CV] n_estimators=64, min_samples_leaf=64, max_features=0.66, max_depth=20 
[CV] n_estimators=64, min_samples_leaf=64, max_features=0.66, max_depth=20 
[CV] n_estimators=64, min_samples_leaf=64, max_features=0.66, max_depth=20 
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=20 
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=20 
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=20 
[CV]  n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=20, total=  30.4s
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=20 
[CV]  n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=20, total=  30.8s
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=20 
[CV]  n_est

[Parallel(n_jobs=8)]: Done  25 tasks      | elapsed:  3.5min


[CV]  n_estimators=32, min_samples_leaf=8, max_features=1.0, max_depth=20, total= 1.0min
[CV] n_estimators=64, min_samples_leaf=32, max_features=0.33, max_depth=32 
[CV]  n_estimators=32, min_samples_leaf=8, max_features=1.0, max_depth=20, total= 1.0min
[CV] n_estimators=64, min_samples_leaf=32, max_features=0.33, max_depth=32 
[CV]  n_estimators=32, min_samples_leaf=8, max_features=1.0, max_depth=20, total= 1.0min
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=None 
[CV]  n_estimators=32, min_samples_leaf=8, max_features=1.0, max_depth=20, total= 1.1min
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=None 
[CV]  n_estimators=64, min_samples_leaf=64, max_features=1.0, max_depth=15, total= 1.5min
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=None 
[CV]  n_estimators=64, min_samples_leaf=32, max_features=0.33, max_depth=32, total=  35.7s
[CV] n_estimators=32, min_samples_leaf=8, max_features=0.5, max_depth=None 
[CV]  n

[Parallel(n_jobs=8)]: Done  50 out of  50 | elapsed:  6.0min finished


RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=False),
          error_score='raise',
          estimator=RandomForestClassifier(bootstrap=True, class_weight='balanced',
            criterion='gini', max_depth=None, max_features='auto',
            max_leaf_nodes=None, min_impurity_decrease=0.0,
            min_impurity_split=None, min_samples_leaf=1,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            n_estimators=10, n_jobs=1, oob_score=False, random_state=42,
            verbose=0, warm_start=False),
          fit_params=None, iid=True, n_iter=10, n_jobs=8,
          param_distributions={'max_depth': [15, 20, 32, None], 'min_samples_leaf': [8, 16, 32, 64], 'max_features': [0.33, 0.5, 0.66, 1.0], 'n_estimators': [32, 64]},
          pre_dispatch='2*n_jobs', random_state=42, refit=True,
          return_train_score='warn', scoring='roc_auc', verbose=2)

In [244]:
print("RF RandomizedSearchCV:\nBest Score: {}\nBest Params: {}".format(gs.best_score_, gs.best_params_))


RF RandomizedSearchCV:
Best Score: 0.7313888532213012
Best Params: {'n_estimators': 64, 'min_samples_leaf': 16, 'max_features': 0.66, 'max_depth': 15}


In [64]:
##Rf with best params
best_rf = RandomForestClassifier(random_state=42,max_depth=20, n_estimators=64, min_samples_leaf=16, max_features=0.5, class_weight='balanced')

In [65]:
scores_best_rf = cross_val_score(estimator=best_rf,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('best rf scoring: {:.5f}'.format(scores_best_rf))

best rf scoring: 0.73301


In [202]:
## Light
import lightgbm as lgb

In [270]:
n_rounds = 10000

lgb_train = lgb.Dataset(x_train, label=y_train, free_raw_data=False)


prev score0.7450974621228335


In [288]:
lgb_param = {
    'objective': 'binary',
    'num_threads': 8,
    "metric": 'auc',
    'learning_rate': 0.001,
    'n_estimators': 10000,
    'num_leaves': 50,
    
    #regularization
    'colsample_bytree': 0.6,
    'subsample': 0.8,
    'subsample_freq': 1,
    'min_data_in_leaf': 50,
    
}

result = lgb.cv(lgb_param, lgb_train, n_rounds, folds=kf.split(x_train, y_train), early_stopping_rounds=170, verbose_eval=0,  )


print("prev score: "+str(lgb_score))
print(max(result['auc-mean']), len(result['auc-mean']))

lgb_score = max(result['auc-mean'])

/media/ext/opt/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py:390: UserWarning: Found `n_estimators` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


prev score: 0.746696799884063
0.7476524581500925 8157


In [257]:

est = lgb.LGBMClassifier(objective='binary', num_threads=8, metric='auc')


In [186]:
est.train()

AttributeError: 'LGBMClassifier' object has no attribute 'train'

In [265]:

param_grid = {

    
    
    #regularization
    'colsample_bytree': [0.8],
    'subsample': [0.8],
    'subsample_freq': [1],
    'min_data_in_leaf': [50]
    
}

gbm = RandomizedSearchCV(est, param_grid, n_jobs=8, cv=kf, n_iter=1000, scoring='roc_auc', verbose=-2, 
                         )

gbm.fit(x_train, y_train)
#print("RF RandomizedSearchCV:\nBest Score: {}\nBest Params: {}".format(gbm.best_score_, gbm.best_params_))

ValueError: The total space of parameters 1 is smaller than n_iter=1000. For exhaustive searches, use GridSearchCV.

In [85]:
## Bagging LR
from sklearn.ensemble import BaggingClassifier

In [95]:
bg = BaggingClassifier(lr, random_state=42, n_estimators=15)

In [120]:
scores_bg = cross_val_score(
    estimator=bg,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('BG scoring: {:.5f}'.format(scores_bg))

BG scoring: 0.72378


In [108]:
##Bagging DT
bg_dt = BaggingClassifier(dt, random_state=42, n_estimators=15)

In [121]:
scores_bg_dt = cross_val_score(
    estimator=bg_dt,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('BG_dt scoring: {:.5f}'.format(scores_bg_dt))

BG_dt scoring: 0.69488


In [122]:
##Bagging RF
bg_rf = BaggingClassifier(rf, random_state=42, n_estimators=15)

In [123]:
scores_bg_rf = cross_val_score(
    estimator=bg_rf,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('BG_rf scoring: {:.5f}'.format(scores_bg_rf))

BG_rf scoring: 0.71966


In [145]:
##Bagging Best RF
bg_best_rf = BaggingClassifier(best_rf, random_state=42, n_estimators=15)

In [146]:
scores_bg_best_rf = cross_val_score(
    estimator=bg_best_rf,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('Best BG_rf scoring: {:.5f}'.format(scores_bg_best_rf))

Best BG_rf scoring: 0.73058


In [72]:
scores = {
    'LR': scores_lr,
    'DT': scores_dt,
    'RF': scores_rf,
    'Fred\'s rf scores': scores_rf_fred,
    'best_rf': scores_best_rf,
    'lgb': lgb_score,
    
    
}
for l, v in scores.items():
    print("{}: {}".format(l, v))

LR: 0.7244195204372661
DT: 0.5354134076385139
RF: 0.6723406224373523
Fred's rf scores: 0.7280361530079127
best_rf: 0.7330074747799471
lgb: 0.7455568612456418


In [132]:
#submit
x_test= test.drop(rejected_variables, axis=1, errors='ignore')
x_test = x_test.drop('0', axis=1)
x_train.shape, x_test.shape

((30500, 339), (4166, 339))

In [274]:

model = lgb.train(lgb_param, lgb_train, num_boost_round=828)

In [275]:
pred = model.predict(x_test)
print(max(pred))

0.8616675663986619


In [276]:
from sklearn.metrics import roc_auc_score
roc_auc_score(y_train, model.predict(x_train))


0.8558763037136785

In [277]:
pred_df= pd.DataFrame({'_ID_': x_test.index, '_VAL_': pred})
pred_df.to_csv('submit1.csv', index=False)

In [160]:
x_train.shape[0]

30500

In [278]:
##Stacking

indices = list(kf.split(x_train, y_train))


new_train_feature = np.zeros(x_train.shape[0])
new_test_feature = np.zeros(x_test.shape[0])


for (i, (sub_train, sub_test)) in enumerate(indices):

    model = lgb.train(lgb_param, lgb_train.subset(sub_train), num_boost_round=867)
    pred = model.predict(x_train.loc[sub_test])
    
    new_train_feature[sub_test] =  pred
   
## adding new feature to test
model2 = lgb.train(lgb_param, lgb_train, num_boost_round=900)
pred2 = model2.predict(x_test)
new_test_feature[:]= pred2

    

In [221]:
x_train.shape, pd.DataFrame(new_train_feature).shape 
pd.concat([x_train, pd.DataFrame(new_train_feature)]).shape

/media/ext/opt/anaconda3/lib/python3.6/site-packages/pandas/core/indexes/api.py:87: RuntimeWarning: '<' not supported between instances of 'str' and 'int', sort order is undefined for incomparable objects
  result = result.union(other)


(61000, 337)

In [279]:
x_train2 = pd.concat([x_train, pd.DataFrame(new_train_feature)], axis=1)
x_test2 = pd.concat([x_test, pd.DataFrame(new_test_feature)], axis=1)

In [230]:

x_test2.head()


1  2  3  4  5  6         7  8  10  11    ...     337  338  339  340  \
0  1  0  0  1  0  0  0.136364  0   1   1    ...       0    1    0    0   
1  1  0  0  1  0  0  0.181818  0   1   1    ...       0    1    0    0   
2  1  0  0  0  0  0  0.090909  0   1   1    ...       0    1    0    0   
3  1  0  0  1  0  0  0.090909  0   1   1    ...       0    1    0    0   
4  1  0  0  1  0  0  0.090909  0   1   1    ...       0    0    1    0   

        341  342  343  344  345         0  
0  0.222222    1    1    1    1  0.340977  
1  0.000000    1    1    1    0  0.421018  
2  0.222222    1    1    1    0  0.397210  
3  0.000000    1    1    1    0  0.388529  
4  0.000000    1    1    1    1  0.483479  

[5 rows x 340 columns]

In [280]:
lgb_train2 = lgb.Dataset(x_train2, y_train, free_raw_data=False)

In [281]:
result = lgb.cv(lgb_param, lgb_train2, 10000, folds=kf.split(x_train2, y_train), early_stopping_rounds=45, verbose_eval=0, )

print(max(result['auc-mean']), len(result['auc-mean']))
lgb_score = max(result['auc-mean'])

0.7406061915162278 18
